In [1]:
#Program to solve 2D Schrodinger equation by using finite-element method

#Unit of length: nm
#Elements are taken equidistantly from the origin
#Rows
#Even: derivative
#Odd: Schrodinger eq
#Columns
#Odd: wave function
#Even: derivative of wf
#

using Distributed #parallel calculation
using BenchmarkTools 

In [2]:
addprocs() 

40-element Vector{Int64}:
  2
  3
  4
  5
  6
  7
  8
  9
 10
 11
 12
 13
 14
  ⋮
 30
 31
 32
 33
 34
 35
 36
 37
 38
 39
 40
 41

In [3]:
nprocs() #number of workers

41

In [4]:
#Read packages
@everywhere using Struve
@everywhere using LinearAlgebra

#Physical canstants
@everywhere const h=1.054571817 #Reduced Planck constant*10^-34
@everywhere const m0=9.10938356 #Electron mass*10^-31
@everywhere const m=0.2*m0 #Reduced mass
@everywhere const e=1.60217662 #Elementary charge*10^-19
@everywhere const ε0=8.85418782 #Permitivity in vacuum*10^-12

In [5]:
#Matrix1
@everywhere function makeA_kappa_r0(N,dx,l,κ,r0)
    A=zeros(Float64, 2*N, 2*N)
    for i in 1:N
        xx=dx*(2*i-1) #{(ri)+(ri+1)}/2
        #微分の式
        if i>1
            A[2*i-1,2*i-2]=0.5 #R'(ri)
        end
        A[2*i-1,2*i-1]=1/dx #R(ri)
        A[2*i-1,2*i  ]=0.5 #R'(ri+1)
        if i<N
            A[2*i-1,2*i+1]=-1/dx #R(ri+1)
        end
        #Schrodinger eq w/ unit of meV
        if i>1
            A[2*i,2*i-2]=0.5*1000*h*h/(e*m*dx)-0.5*1000*h*h/(e*m*xx)  #R'(ri)
        end
        A[2*i,2*i-1]=1000*h*h*l*l/(e*m*xx*xx)+0.5*potential_kappa_r0(xx/2,κ,r0) #R(ri)
        A[2*i,2*i  ]=-0.5*1000*h*h/(e*m*dx)-0.5*1000*h*h/(e*m*xx) #R'(ri+1)
        if i<N
            A[2*i,2*i+1]=1000*h*h*l*l/(e*m*xx*xx)+0.5*potential_kappa_r0(xx/2,κ,r0) #R(ri+1)
        end
    end
    return A
end

#Matrix2
@everywhere function makeB(N,dx)
    B=zeros(Float64, 2*N, 2*N)
    
    for i in 1:N
        B[2*i,2*i-1]=0.5
        if i<N
            B[2*i,2*i+1]=0.5
        end
    end
    return B
end

#Rytova-Keldysh potential
@everywhere function potential_kappa_r0(r,κ,r0)
#    e=1.60217662
#    ε0=8.85418782
    return -10^5*e*Struve.K0(κ*r/r0)/(8*ε0*r0)
end

#Calculation & record of Schrodinger eq
@everywhere function SolveProblem(N,dx,l,κ,r0)
    A=makeA_kappa_r0(N,dx,l,κ,r0)
    B=makeB(N,dx)
    F=eigen(A,B)

    fp1=open(string("eigenvalues_N", N ,"_dx", dx ,"_L", l , "_κ", κ , "_r0_" , r0 ,".dat"),"w")
    for i=1:10
        s=string(F.values[i])
        println(fp1, s)
    end
    close(fp1)
    
    #Record eigenvectors
    fp2=open(string("eigenvectors_N", N ,"_dx", dx ,"_L", l , "_κ", κ , "_r0_" , r0 ,".dat"),"w")
    for i=1:N
        s=""
        for j=1:10#(2*N)
            s=string(s, F.vectors[2*i-1,j],"\t")
        end
        println(fp2, s)
    end
    close(fp2)
    
    return F.values
end

#Serial calculation
function SerialCalculation(N,dx, L0,dL,NL, κ0,dκ,Nκ, r0_0,dr0,Nr0)
    
    for i in 1:NL
        for j in 1:Nκ
            for k in 1:Nr0
                SolveProblem(N, dx, L0+dL*i, κ0+dκ*j, r0_0+dr0*k)
            end
        end
    end
end

#Parallel calculation
function ParallelCalculation(N,dx, L0,dL,NL, κ0,dκ,Nκ, r0_0,dr0,Nr0)
    Ns=[N for i in 0:(NL*Nκ*Nr0-1)]
    dxs=[dx for i in 0:(NL*Nκ*Nr0-1)]
    Ls=[L0+dL*floor(i/(Nκ*Nr0)) for i in 0:(NL*Nκ*Nr0-1)]
    κs=[κ0+dκ*mod(floor(i/Nr0),Nκ) for i in 0:(NL*Nκ*Nr0-1)]
    r0s=[r0_0+dr0*mod(i,Nr0) for i in 0:(NL*Nκ*Nr0-1)]
#    println("Ns=",Ns)
#    println("dxs=",dxs)
#    println("Ls=",Ls)
#    println("κs=",κs)
#    println("r0s=",r0s)
    return pmap(SolveProblem, Ns,dxs,Ls,κs,r0s)
end

ParallelCalculation (generic function with 1 method)

In [6]:
#@time SerialCalculation(200,0.05, 0,1,3, 4,0.1,5, 4,0.1,5)

In [6]:
@time ParallelCalculation(2000,0.05, 0,1,2, 2.,0.01,1, 2.,0.01,1)

1137.647010 seconds (863.64 k allocations: 57.015 MiB, 0.00% gc time, 0.09% compilation time: 2% of which was recompilation)


2-element Vector{Vector{Float64}}:
 [-Inf, -Inf, -Inf, -Inf, -Inf, -Inf, -Inf, -Inf, -Inf, -Inf  …  Inf, Inf, Inf, Inf, Inf, Inf, Inf, Inf, Inf, Inf]
 [-Inf, -Inf, -Inf, -Inf, -Inf, -Inf, -Inf, -Inf, -Inf, -Inf  …  Inf, Inf, Inf, Inf, Inf, Inf, Inf, Inf, Inf, Inf]

In [9]:
makeA_kappa_r0(2000,0.05,0,4,4)

4000×4000 Matrix{Float64}:
   20.0        0.5    -20.0        0.0   …      0.0     0.0          0.0
 -689.214  -7619.96  -689.214      0.0          0.0     0.0          0.0
    0.0        0.5     20.0        0.5          0.0     0.0          0.0
    0.0     2539.99  -499.657  -5079.98         0.0     0.0          0.0
    0.0        0.0      0.0        0.5          0.0     0.0          0.0
    0.0        0.0      0.0     3047.99  …      0.0     0.0          0.0
    0.0        0.0      0.0        0.0          0.0     0.0          0.0
    0.0        0.0      0.0        0.0          0.0     0.0          0.0
    0.0        0.0      0.0        0.0          0.0     0.0          0.0
    0.0        0.0      0.0        0.0          0.0     0.0          0.0
    0.0        0.0      0.0        0.0   …      0.0     0.0          0.0
    0.0        0.0      0.0        0.0          0.0     0.0          0.0
    0.0        0.0      0.0        0.0          0.0     0.0          0.0
    ⋮                   